高频交易与中低频的不同

对于中低频的趋势交易策略，如果交易量不是很大的话，单个交易策略对市场的影响微乎其微，可以只考虑市场什么情况，在这种情况下，考虑交易成本之后，回测有一定的可靠性。

高频的交易，本身可能对这个市场就有很大的影响，自身的行为就可能导致市场行为发生改变，使用历史data_folder回测，即使不考虑交易成本，也很难得到准确的结果。

用python去回测tickdata_folder的不足

python作为一门解释性语言，相对于C++等编译性语言，运行速度会慢上好多。而tickdata_folder本身data_folder量就比较多，导致python写的量化框架，回测tickdata_folder的时候，都需要耗时比较多。

由于框架自带了丰富的信息，会导致在运行的过程中，内存会不断增大，如果回测的tickdata_folder比较多，几十个G的内存很有可能不够。

总结一下，使用python本身速度比较慢，用来高频回测会额外消耗内存，导致回测大量的tickdata_folder变得又慢又占内存。

因此，这里只是演示一下怎么用这个框架进行tickdata_folder回测，但不建议实际这么操作（早知道写成c++的框架了。。。可惜时间不够

1. 期货的tickdata_folder，都包含这些内容

localtime (本机写入TICK的时间),
InstrumentID (合约名),
TradingDay (交易日),
ActionDay (业务日期),
UpdateTime （时间）,
UpdateMillisec（时间毫秒）,
LastPrice （最新价）,
Volume（成交量） ,
HighestPrice （最高价）,
LowestPrice（最低价） ,
OpenPrice（开盘价） ,
ClosePrice（收盘价）,
AveragePrice（均价）,
AskPrice1（申卖价一）,
AskVolume1（申卖量一）,
BidPrice1（申买价一）,
BidVolume1（申买量一）,
UpperLimitPrice（涨停板价）
LowerLimitPrice（跌停板价）
OpenInterest（持仓量）,
Turnover（成交金额）,
PreClosePrice (昨收盘),
PreOpenInterest (昨持仓),
PreSettlementPrice (上次结算价),

2. 在回测的时候需要传入的data_folder


传入data_folder的时候，一般都是需要使用到open\high\low\close这四个价格，为了符合回测的逻辑，让最新价等于open\high\low\close，并且可以额外添加几个列，比如AskVolume1(卖量一）,BidVolume1(买量一)。

这样做有一个缺陷：使用限价单的时候，其实并不能知道能不能成交。比如价格6元的买订单，最新价在5.9元的时候，是会成交的，但是并不能知道最新价在6.00的时候会不会成交。这是一个缺陷。

如果想要避免这个，就需要开发逐tick回测的模式。

目前这个只是基于bar进行的改造，是对现实的一个逼近。理论上是存在更好的回测方法的。

In [2]:
import pandas as pd
import numpy as np
data = pd.read_csv("./future/rb2105_raw_data.csv")
data['datetime']=pd.to_datetime([str(x)+" "+str(y)+"."+str(z) for x,y,z in zip(data['ActionDay'], data["UpdateTime"],data['UpdateMillisec'])])
data['open'] = data['LastPrice']
data['close'] = data['LastPrice']
data['high'] = data['LastPrice']
data['low'] = data['LastPrice']
data['volume'] = data['Volume']
data= data[['datetime','open','high','low','close','volume','AskPrice1','AskVolume1','BidPrice1','BidVolume1']]
data.to_csv("./future/rb2105.csv",index=False)

In [7]:
import backtesting as bt
from backtrader import num2date
import datetime
import pyfolio as pf
import warnings
warnings.filterwarnings('ignore')
# 在交易信息之外，额外增加了PE、PB指标，做涉及到基本面信息的策略使用
class GenericTickCSV(bt.feeds.GenericCSVData):

    # 增加两个line,每个line的名称，就是csv文件中，额外增加的列的名称
    lines = ('AskPrice1','AskVolume1','BidPrice1','BidVolume1',)

    # 具体每个新增加的变量index是多少，要根据自己的csv文件去决定，从0开始数
    params = (('AskPrice1',6),('AskVolume1',7),('BidPrice1',8),('BidVolume1',9))
    
# 我们使用的时候，直接用我们新的类读取data_folder就可以了。
class TestTickStrategy(bt.Strategy):
   
    params = (('window',200),)

    def log(self, txt, dt=None):
        ''' Logging function fot this strategy'''
        dt = dt or num2date(self.datas[0].datetime[0])
        print('{}, {}'.format(dt.isoformat(), txt))

    def __init__(self):
        # Keep a reference to the "close" line in the data[0] dataseries
        self.bar_num=0
        # 持仓状态
        self.marketposition = 0
        # 订单的初始值
        self.buy_order = None
        self.sell_order = None
       
    def prenext(self):
        
        pass 
        
    def next(self):
        # 假设有100万资金，每次成份股调整，每个股票使用1万元
        self.bar_num+=1
        # 获取并打印当前的data_folder
        data = self.datas[0]
        now_datetime = num2date(data.datetime[0])
        now_open = data.open[0]
        now_high = data.high[0]
        now_low = data.low[0]
        now_close = data.close[0]
        # 卖一价、量
        now_ask_volume = data.AskVolume1[0]
        now_ask_price = data.AskPrice1[0]
        # 买一价、量
        now_bid_price = data.BidPrice1[0]
        now_bid_volume = data.BidVolume1[0]
        # 输出信息
        self.log(f"now_open\high\low\close\lastprice:{now_open},\
                now_ask_volume:{now_ask_volume},\
                now_ask_volume:{now_ask_volume},\
                now_bid_price:{now_bid_price},\
               now_bid_volume:{now_bid_volume}")
        hold_size = self.getposition(data).size
        # 平仓
        if  self.bar_num%120 == 0:
            
            # 限价买单没成交
            if self.buy_order is not None and self.marketposition == 1:
                self.cancel(self.buy_order)
                self.buy_order = None
            # 限价卖单没成交
            if self.sell_order is not None and hold_size>0:
                self.cancel(self.sell_order)
                self.sell_order = None
                # 平仓
                self.close()
            self.marketposition = 0 
        # 开仓
        if hold_size == 0 and self.marketposition==0 and self.bar_num%120==0:
            
            self.buy_order = self.buy(self.datas[0],size = 1,exectype=bt.Order.Limit,price = now_bid_price-1)
            self.marketposition = 1
        # 限价单平仓
        if self.marketposition == 1 and hold_size>0 and  self.bar_num%120!=0:
           
            self.sell_order = self.sell(self.datas[0],size = 1,exectype=bt.Order.Limit,price = now_ask_price+2)
            self.marketposition = 0
            
            
    def notify_order(self, order):
        
        if order.status in [order.Submitted, order.Accepted]:
            return
        
        if order.status == order.Rejected:
            self.log(f"Rejected : order_ref:{order.ref}  data_name:{order.p.data._name}")
            
        if order.status == order.Margin:
            self.log(f"Margin : order_ref:{order.ref}  data_name:{order.p.data._name}")
            
        if order.status == order.Cancelled:
            self.log(f"Concelled : order_ref:{order.ref}  data_name:{order.p.data._name}")
            
        if order.status == order.Partial:
            self.log(f"Partial : order_ref:{order.ref}  data_name:{order.p.data._name}")
         
        if order.status == order.Completed:
            if order.isbuy():
                self.log(f" BUY : data_name:{order.p.data._name} price : {order.executed.price} , cost : {order.executed.value} , commission : {order.executed.comm}")

            else:  # Sell
                self.log(f" SELL : data_name:{order.p.data._name} price : {order.executed.price} , cost : {order.executed.value} , commission : {order.executed.comm}")
    
    def notify_trade(self, trade):
        # 一个trade结束的时候输出信息
        if trade.isclosed:
            self.log('closed symbol is : {} , total_profit : {} , net_profit : {}' .format(
                            trade.getdataname(),trade.pnl, trade.pnlcomm))
            # self.trade_list.append([self.datas[0].datetime.date(0),trade.getdataname(),trade.pnl,trade.pnlcomm])
            
        if trade.isopen:
            self.log('open symbol is : {} , price : {} ' .format(
                            trade.getdataname(),trade.price))
    def stop(self):
        
        pass 
        
        
        
    
params = dict(
            fromdate = datetime.datetime(2021,1,4), # 回测开始时间
            todate = datetime.datetime(2021,3,20),  # 回测结束时间
            timeframe = bt.TimeFrame.Ticks,
            compression = 1,
            dtformat=('%Y-%m-%d %H:%M:%S.%f'), # 日期和时间格式
            tmformat=('%H:%M:%S.%f'), # 时间格式
            datetime=0, # 下面几行是导入的data_folder，要和传入的data_folder列进行一一对应，以这个参数为准
            high=2,
            low=3,
            open=1,
            close=4,
            volume=5,
            openinterest=-1)


     
# 初始化cerebro,获得一个实例
cerebro = bt.Cerebro()
# cerebro.broker = bt.brokers.BackBroker(shortcash=True)  # 0.5%
# 读取data_folder
feed = GenericTickCSV(dataname = "./future/rb2105.csv",**params)
# 添加data_folder到cerebro
cerebro.adddata(feed, name = "rb2105")
# 添加手续费，按照万分之五收取
cerebro.broker.setcommission(commission=0.0005,stocklike=False)
# 设置初始资金为100万
cerebro.broker.setcash(1000000.0)
# 添加策略
cerebro.addstrategy(TestTickStrategy)
# 运行回测
cerebro.run()
print('Final Portfolio Value: %.2f' % cerebro.broker.getvalue())


2021-02-08T20:59:00.500000, now_open\high\low\close\lastprice:4335.0,                now_ask_volume:141.0,                now_ask_volume:141.0,                now_bid_price:4335.0,               now_bid_volume:76.0
2021-02-08T21:00:00.499997, now_open\high\low\close\lastprice:4335.0,                now_ask_volume:27.0,                now_ask_volume:27.0,                now_bid_price:4335.0,               now_bid_volume:16.0
2021-02-08T21:00:01, now_open\high\low\close\lastprice:4335.0,                now_ask_volume:200.0,                now_ask_volume:200.0,                now_bid_price:4333.0,               now_bid_volume:20.0
2021-02-08T21:00:01.500001, now_open\high\low\close\lastprice:4336.0,                now_ask_volume:160.0,                now_ask_volume:160.0,                now_bid_price:4335.0,               now_bid_volume:60.0
2021-02-08T21:00:02, now_open\high\low\close\lastprice:4336.0,                now_ask_volume:4.0,                now_ask_volume:4.0,                n